In [ ]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.functions import col, explode, size, array_distinct,collect_list,expr, array_contains, rank,lower,avg, expr, when,mean,split,first,array
import pandas as pd
import matplotlib.pyplot as plt
from pyspark.ml.feature import VectorAssembler, StringIndexer

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)

spark = SparkSession.builder.getOrCreate()

In [ ]:
profiles = spark.read.parquet('/linkedin/people')
profiles.display()

about avatar certifications city country_code current_company current_company:company_id current_company:name education educations_details experience followers following groups id languages name people_also_viewed position posts recommendations recommendations_count timestamp url volunteer_experience сourses null https://static.licdn.com/aero-v1/sc/h/244xhbkr7g40x6bsu4gi6q4ry List() Sunnyside, Washington, United States US List(sunnyside-unified-school-district, Sunnyside Unified School District, https://eg.linkedin.com/company/sunnyside-unified-school-district?trk=public_profile_topcard-current-company, Sunnyside Unified School District, Special Services Director at Sunnyside Unified School District) sunnyside-unified-school-district Sunnyside Unified School District List() null List(List(null, null, null, null, null, null, null, null, null, Sunnyside Unified School District, https://eg.linkedin.com/company/sunnyside-unified-school-district?trk=public_profile_experience-item_profile-section-card_subtitle-click, Special Services Director, null)) 1 1 List() cody-gardiner-7a039667 List() cody gardiner List() Special Services Director at Sunnyside Unified School District List() List() null 2023-09-04 https://www.linkedin.com/in/cody-gardiner-7a039667 List() List() null https://static.licdn.com/aero-v1/sc/h/244xhbkr7g40x6bsu4gi6q4ry List() Spring, Texas, United States US List(null, N/A, null, N/A, Retired at N/A) null N/A List(List(Bachelor of Arts (BA), 1963, Elementary Education and Teaching, 1959 - 1963, 1959, Baylor University, https://www.linkedin.com/school/baylor-university/?trk=public_profile_school_profile-section-card_image-click)) Baylor University List(List(null, null, null, null, null, null, null, null, null, N/A, null, Retired, null)) 13 13 List() sharon-tunnell-436474104 List() Sharon Tunnell List() Retired at N/A List() List() null 2023-09-04 https://www.linkedin.com/in/sharon-tunnell-436474104 List() List() null https://static.licdn.com/aero-v1/sc/h/244xhbkr7g40x6bsu4gi6q4ry List() United States US List(null, null, null, null, --) null null List() null List() 62 62 List() teresa-fulford-25a59a4b List() Teresa Fulford List() -- List() List() null 2023-09-04 https://www.linkedin.com/in/teresa-fulford-25a59a4b List() List() hard worker goal oriented and willing to work https://static.licdn.com/aero-v1/sc/h/244xhbkr7g40x6bsu4gi6q4ry List() Cleveland, Ohio, United States US List(dfas, DFAS, https://cn.linkedin.com/company/dfas?trk=public_profile_topcard-current-company, DFAS, Military Pay Technician at DEFENSE FINANCE AND ACCOUNTING SERVICE-CLEVELAND Retired Annuitant Pay Cleveland Ohio) dfas DFAS List(List(null, 2005, null, 2004 - 2005 Received training in radio and television broadcast and production techniques. Skilled in operation of various audio and video studio equipment. Hands-on experience with Cool-Edit audio workstation. Practice with copy and news writing skills. Have maintained perfect attendance., 2004, OHIO CENTER FOR BROADCASTING, null), List(Bachelor of General Studies, 1999, General Studies of Art & Science, 1994 - 1999 Activities: Kent Interhall Council, Channels 45/49 Public Television, TV2, and Black United Students., 1994, Kent State University, https://cn.linkedin.com/school/kent-state-university/?trk=public_profile_school_profile-section-card_image-click)) OHIO CENTER FOR BROADCASTING List(List(DFAS, dfas, null, 14 years 8 months, null, null, null, List(List(Responsible for handling retired military pay accounts and answering the phone from Members, Annuitant and former spouse., Feb 2009 - Present 14 years 8 months, 14 years 8 months, Present, Feb 2009 - Present14 years 8 months , Responsible for handling retired military pay accounts and answering the phone from Members, Annuitant and former spouse., Feb 2009, DFAS, Military Pay Technician), List(Responsible for handling retired military pay accounts and answering the phone from Members, Annuitant and former spouse., Feb 2009 - Present 14 years 

In [ ]:
users = profiles.withColumnRenamed("current_company:name","c_name")
users = users.withColumn("c_name", lower(users["c_name"]))
l = ['yahoo','google','nvidia','microsoft','meta','amazon','apple','intel','oracle','zoom','netflix','spotify','sap','dell','tesla','cisco','linkedin','adobe','qualcomm','amd']

users.filter(users['c_name'] == 'google').select("position").distinct().show(100,truncate=False)

+---------------------------------------------------------------------------------------------------------------------------------+
|position                                                                                                                         |
+---------------------------------------------------------------------------------------------------------------------------------+
|Senior Software Engineer at Google                                                                                               |
|Engineering Manager at Google Search                                                                                             |
|Startup Marketing Manager for Google Cloud                                                                                       |
|Graduate Student at Google                                                                                                       |
|Technical Program Manager                                                  

In [ ]:
#print(users.filter(users['c_name'] == 'intel').count())
FAANG_users = users.filter(users['c_name'].isin(l))
#target_users.display()
print(FAANG_users.count())


14718


In [ ]:
FAANG_users = FAANG_users.withColumn("position_small", lower(col("position")))
words = ["engineer", "cloud", "software", "aiml", "engineering","data", "machine learning","ml","quality assurance","qa","r&d","cyber","security"]
tech_users = FAANG_users.filter(col("position_small").rlike("|".join(words)))

words_to_exclude = ["marketing", "sales", "artist","dei", "helpdesk","assistant","secretary", "null","account","accounts","accounting","area","retired", "human","social","student","manager","art"]
tech_users = tech_users.filter(~col("position_small").rlike("|".join(words_to_exclude)))

positions_list = tech_users.select("position_small").rdd.map(lambda row: row[0]).collect()
#print(len(positions_list))
tech_users.count()
#tech_users =tech_users.select("id","position","url")
#tech_users.sample(fraction=0.0014, seed=42).show(truncate=False)

Out[13]: 4513